In [1]:
# This is necessary to recognize the modules
import os
import sys


root_path = os.path.abspath(os.path.join(os.getcwd(), '../..'))
sys.path.append(root_path)


In [2]:
from plotly.subplots import make_subplots
import pandas as pd
import numpy as np
import plotly.graph_objects as go

from hummingbot.connector.connector_base import TradeType


def get_bt_candlestick_trace(df):
    df.index = pd.to_datetime(df.timestamp, unit='s')
    return go.Scatter(x=df.index,
                      y=df['close'],
                      mode='lines',
                      line=dict(color="blue"),
                      )


def get_pnl_trace(executors):
    pnl = [e.net_pnl_quote for e in executors]
    cum_pnl = np.cumsum(pnl)
    return go.Scatter(
        x=pd.to_datetime([e.close_timestamp for e in executors], unit="s"),
        y=cum_pnl,
        mode='lines',
        line=dict(color='gold', width=2, dash="dash"),
        name='Cumulative PNL'
    )


def get_default_layout(title=None, height=800, width=1800):
    layout = {
        "template": "plotly_dark",
        "plot_bgcolor": 'rgba(0, 0, 0, 0)',  # Transparent background
        "paper_bgcolor": 'rgba(0, 0, 0, 0.1)',  # Lighter shade for the paper
        "font": {"color": 'white', "size": 12},  # Consistent font color and size
        "height": height,
        "width": width,
        "margin": {"l": 20, "r": 20, "t": 50, "b": 20},
        "xaxis_rangeslider_visible": False,
        "hovermode": "x unified",
        "showlegend": False,
    }
    if title:
        layout["title"] = title
    return layout


def add_executors_trace(fig, executors, row, col):
    for executor in executors:
        entry_time = pd.to_datetime(executor.timestamp, unit='s')
        entry_price = executor.custom_info["current_position_average_price"]
        exit_time = pd.to_datetime(executor.close_timestamp, unit='s')
        exit_price = executor.custom_info["close_price"]
        name = "Buy Executor" if executor.config.side == TradeType.BUY else "Sell Executor"

        if executor.filled_amount_quote == 0:
            fig.add_trace(go.Scatter(x=[entry_time, exit_time], y=[entry_price, entry_price], mode='lines',
                                     line=dict(color='grey', width=2, dash="dash"), name=name), row=row, col=col)
        else:
            if executor.net_pnl_quote > Decimal(0):
                fig.add_trace(go.Scatter(x=[entry_time, exit_time], y=[entry_price, exit_price], mode='lines',
                                         line=dict(color='green', width=4), name=name), row=row, col=col)
            else:
                fig.add_trace(go.Scatter(x=[entry_time, exit_time], y=[entry_price, exit_price], mode='lines',
                                         line=dict(color='red', width=4), name=name), row=row, col=col)

    return fig


def create_backtesting_figure(df, executors, config):
    # Create subplots
    fig = make_subplots(rows=2, cols=1, shared_xaxes=True,
                        vertical_spacing=0.02, subplot_titles=('Candlestick', 'PNL Quote'),
                        row_heights=[0.7, 0.3])

    # Add candlestick trace
    fig.add_trace(get_bt_candlestick_trace(df), row=1, col=1)

    # Add executors trace
    fig = add_executors_trace(fig, executors, row=1, col=1)

    # Add PNL trace
    fig.add_trace(get_pnl_trace(executors), row=2, col=1)

    # Apply the theme layout
    layout_settings = get_default_layout(f"Trading Pair: {config['trading_pair']}")
    layout_settings["showlegend"] = False
    fig.update_layout(**layout_settings)

    # Update axis properties
    fig.update_xaxes(rangeslider_visible=False, row=1, col=1)
    fig.update_xaxes(row=2, col=1)
    fig.update_yaxes(title_text="Price", row=1, col=1)
    fig.update_yaxes(title_text="PNL", row=2, col=1)
    return fig

In [14]:
import pickle

import pandas as pd
path = os.path.join(root_path, "research_notebooks", "xtreet_bb", "backtesting_results_2.pickle")

bt_results = pickle.load(open(path, 'rb'))

In [15]:
import pandas as pd

results_df = pd.DataFrame([result["results"] for result in bt_results.values()])
results_df

net_pnl  net_pnl_quote  total_executors  \
0    -0.00484196    -4.84195694              417   
1     0.00190601     1.90600733              172   
2    -0.00058755    -0.58755052              113   
3     0.00065077     0.65076917              156   
4     -0.0001435    -0.14350343              205   
...          ...            ...              ...   
1131  0.00768323     7.68322574              309   
1132 -0.00210125    -2.10125064              391   
1133  0.02881535    28.81534883              295   
1134 -0.00293144    -2.93144282              163   
1135  0.00226572     2.26572167              248   

      total_executors_with_position   total_volume  total_long  total_short  \
0                               406 85002.47659906         210          196   
1                               165   679.63356405          97           68   
2                               110   720.49746284          61           49   
3                               147  19572.7608954          76           71   
4                               202   947.47336926         125           77   
...                             ...            ...         ...          ...   
1131                            304 46299.38949939         184          120   
1132                            382 45000.65578428         239          143   
1133                            282 62021.87588328         158          124   
1134                            161  1320.50314089         100           61   
1135                            242 40819.09594014         121          121   

                                            close_types  accuracy_long  \
0     {'STOP_LOSS': 156, 'TAKE_PROFIT': 250, 'TIME_L...     0.58095238   
1                {'TAKE_PROFIT': 146, 'TIME_LIMIT': 26}     0.86597938   
2     {'STOP_LOSS': 1, 'TAKE_PROFIT': 86, 'TIME_LIMI...     0.75409836   
3     {'STOP_LOSS': 49, 'TAKE_PROFIT': 97, 'TIME_LIM...     0.64473684   
4     {'STOP_LOSS': 1, 'TAKE_PROFIT': 178, 'TIME_LIM...           0.92   
...                                                 ...            ...   
1131  {'STOP_LOSS': 58, 'TAKE_PROFIT': 243, 'TIME_LI...     0.80978261   
1132  {'STOP_LOSS': 52, 'TAKE_PROFIT': 329, 'TIME_LI...     0.87866109   
1133  {'STOP_LOSS': 85, 'TAKE_PROFIT': 196, 'TIME_LI...     0.69620253   
1134  {'STOP_LOSS': 1, 'TAKE_PROFIT': 140, 'TIME_LIM...           0.88   
1135  {'STOP_LOSS': 60, 'TAKE_PROFIT': 181, 'TIME_LI...     0.72727273   

      accuracy_short  total_positions   accuracy  max_drawdown_usd  \
0         0.65306122              406 0.61576355       -9.17081089   
1         0.91176471              165 0.88484848        -0.2028611   
2         0.81632653              110 0.78181818       -0.69533101   
3         0.69014085              147 0.66666667       -2.43810015   
4         0.84415584              202 0.89108911       -0.60815388   
...              ...              ...        ...               ...   
1131      0.79166667              304 0.80263158       -12.7433636   
1132      0.83216783              382 0.86125654      -15.25384581   
1133       0.7016129              282 0.69858156       -7.70228398   
1134      0.86885246              161  0.8757764       -3.02988932   
1135      0.76859504              242 0.74793388       -4.30788502   

      max_drawdown_pct  sharpe_ratio  profit_factor  win_signals  \
0          -0.00917586   -0.11193606     0.94557752          250   
1          -0.00020286    1.33836356     3.50471649          146   
2          -0.00069532   -1.23972393       0.634735           86   
3          -0.00243928    0.15220614     1.03761004           98   
4          -0.00060818    -0.6823067       0.907402          180   
...                ...           ...            ...          ...   
1131       -0.01274104   -0.49346572     1.10299639          244   
1132       -0.01525266   -0.04255869     0.96701701          329   
1133       -0.00769411     0.8594206     1.28866707          197   
1134       -0.00302986   

In [16]:
import plotly.express as px

# Create a new column with custom hover text
results_df['custom_hover_text'] = results_df.apply(lambda row: f"""
Pair: {row['config']['trading_pair']}
<br>Volume: {row['total_volume']}
<br>PNL: {row['net_pnl_quote']}
<br>Close types: {row['close_types']}

Config:
<br>Id: {row['config']['id']}
<br>BB Length: {row['config']['bb_length']}
<br>BB Std: {row['config']['bb_std']}
<br>Take profit: {row['config']['take_profit']}
<br>Stop loss: {row['config']['stop_loss']}
<br>Time limit: {row['config']['time_limit']}
<br>DCA Spreads: {row['config']['dca_spreads']}
<br>DCA Amounts: {row['config']['dca_amounts_pct']}
""", axis=1)

# Create the scatter plot with the custom hover text
fig = px.scatter(
    results_df,
    x="total_volume",
    y="net_pnl_quote",
    color="trading_pair",  # Color by trading_pair
    hover_data={"custom_hover_text": True},  # Show the custom hover text
    color_discrete_sequence=px.colors.qualitative.Plotly,  # Optional: use a specific color sequence
    title="Net PNL Quote vs. Total Volume by Trading Pair"
)

# Show the figure
fig.show()


In [18]:
result = bt_results[results_df.sort_values("net_pnl_quote", ascending=False).iloc[0]["config"]["id"] + ".yml"]

In [20]:
from pprint import pprint
from decimal import Decimal

df = result["df"]
config = result["config"]
executors = result["executors"]


fig = create_backtesting_figure(
    df=df,
    executors=executors,
    config=config.dict())
# df.ta.bbands(length=config.bb_length, std=config.bb_std, append=True)
fig.add_trace(go.Scatter(x=df.index,
                         y=df[f"BBU_{config.bb_length}_{config.bb_std}"],
                         line=dict(color='lightblue', width=1))
              )
# fig.add_trace(go.Scatter(x=df.index,
#                          y=df[f"BBM_{config.bb_length}_{config.bb_std}"])
#               )
fig.add_trace(go.Scatter(x=df.index,
                         y=df[f"BBL_{config.bb_length}_{config.bb_std}"],
                         line=dict(color='lightblue', width=1))
                         )
pprint(config)
fig.update_layout(width=1400)
fig.show()

XtreetBBControllerConfig(id='xtreet_bb_binance_perpetual_1m_CRV-USDT_0.0_0.004_0.008_0.008_50_1.0_0.010452961672473877_0.007722007722007728', controller_name='xtreet_bb', controller_type='directional_trading', manual_kill_switch=None, candles_config=[CandlesConfig(connector='binance_perpetual', trading_pair='CRV-USDT', interval='1m', max_records=50)], connector_name='binance_perpetual', trading_pair='CRV-USDT', total_amount_quote=Decimal('142.85714285714286'), max_executors_per_side=1, cooldown_time=0, leverage=20, position_mode=<PositionMode.HEDGE: 'HEDGE'>, stop_loss=Decimal('0.010452961672473877'), take_profit=Decimal('0.007722007722007728'), time_limit=28800, take_profit_order_type=<OrderType.LIMIT: 2>, trailing_stop=TrailingStop(activation_price=Decimal('0.015'), trailing_delta=Decimal('0.003')), candles_connector='binance_perpetual', candles_trading_pair='CRV-USDT', interval='1m', bb_length=50, bb_std=1.0, bb_long_threshold=0.0, bb_short_threshold=1.0, dca_spreads=[Decimal('0.0')